# MOLEARN ANALYSIS TUTORIAL

In [52]:
THIS SCRIPT IS USED TO GET RMSD AND DOPE OF THE WHOLE DATASET, NOT SPLIT IN TRAINING AND VALIDATION

SyntaxError: invalid syntax (360422646.py, line 1)

## Introduction

[molearn](https://github.com/Degiacomi-Lab/molearn) is a Python package streamlining the implementation of machine learning models trainable on protein conformational spaces. This tutorial is dedicated to demonstrating the first principles of analysing the performance of a trained neural network. Implementations of what described below is available in the `MolearnAnalysis` class. You can find out how to use this class in the [molearn_GUI.ipynb](molearn_GUI.ipynb) notebook.

This tutorial is divided in the following sections:

[1. Load neural network and training set](#ref1)
   - [1.1. The data](#ref11)
   - [1.2. Data loading](#ref12)
   - [1.3. Loading the neural network](#ref13)
   
   
[2. Projection into latent space and back](#ref2)
 
 
[3. Dataset analysis](#ref3)
   -  [3.1. RMSD (or MSE) of input vs autoencoded](#ref31)
   -  [3.2. DOPE score of input vs autoencoded](#ref32)
   
   
[4. Full latent space characterization](#ref4)
   - [4.1. Evaluate re-encoding error](#ref41)
   - [4.2. Evaluate DOPE score](#ref42)

To get started, let's load some packages!

In [ ]:
import sys, os, glob
from copy import deepcopy

import numpy as np
import matplotlib.pyplot as plt

import torch.nn as nn
import torch.nn.functional as F
import torch.optim

import nglview as nv
import MDAnalysis as mda
import warnings
warnings.filterwarnings("ignore")

import modeller
from modeller import *
from modeller.scripts import complete_pdb

import biobox as bb

from tqdm import tqdm
#edit path as required for your computer (or remove, if you installed molearn via conda-forge)
sys.path.insert(0, f"C:{os.sep}Users{os.sep}xdzl45{os.sep}workspace{os.sep}molearn{os.sep}src") 

import molearn
from molearn.models.foldingnet import AutoEncoder
device = torch.device('cuda') if torch.cuda.is_available() else torch.device('cpu')

import pandas as pd


## 1. Load neural network and training set <a class="anchor" id="ref1"></a>

### 1.1. the data <a class="anchor" id="ref11"></a>

MurD is a 47-kDa ATP-driven ligase responsible for the biosynthesis of a bacterial peptidoglycan precursor (UDP-N-acetylmuramoyl-L-alanyl-D-glutamate). When bound to its ligand, UDP-N-acetylmuramoyl-L-alanyl-D-alanine, MurD is stabilized in a closed conformation (PDB: [3UAG](https://www.rcsb.org/structure/3UAG)). In the absence of UDP-N-acetylmuramoyl-L-alanyl-D-alanine, MurD takes instead an open conformation (PDB: [1E0D](https://www.rcsb.org/structure/1E0D)). We have carried out molecular dynamics simulations of both states. For this tutorial, we will load a multi-PDB file containing a subset of conformations of both trajectories.

Let's start by defining the files containing the training set (variable `open_file` and `closed_file`), and test set (variable `test_set_file`).

The open_file and closed_file contain training set MD simulations of the closed and open states.

By taking the closed conformation and manually removing the ligand, the protein switches to an open conformation. This is the simulation we will used as test set.

### 1.2. data loading <a class="anchor" id="ref12"></a>

We will now prepare the training set, transforming into a `torch.Tensor` making sure to extract from it only the atoms actually used during neural network training (CA, C, N, O, CB). The following cell yields a PDBData class with attributes:
 - `PDBData.dataset`, a pyTorch `Tensor` containing a desired subset of *normalized* atomic coordinates ready for submission to the neural network.
 - `PDBData.mean` and `PDBData.std`, the mean and standard deviation of the original input data, useful to rescale generated structures into atomic coordinates.
 - `PDBData.get_atominfo()` method that returns a list containing the names, resid, and resname of atoms in the training set (in the same order)
 - `PDBData.mol`, a  `biobox` instance corresponding to the coordinates in `PDBData.dataset`, useful as a PDB writer and offering useful helper functions, e.g. RMSD calculation.


In [53]:
data = molearn.PDBData()
data.import_pdb('alignToOneHelix.pdb')
#data.import_pdb(closed_file) # this will append closed_file structures onto open_files
data.atomselect(atoms=['CA', 'C', 'CB', 'N', 'O'])
data.prepare_dataset()

training_set = data.dataset
stdval = data.std
meanval = data.mean
mol = data.mol
atom_names = data.get_atominfo()

Dataset.shape: torch.Size([1427, 3, 308])
mean: 77.28264257501434, std: 30.71670672686316


`training_set` takes the form of a Nx3xM normalised `Tensor` object, where N is the number of examples, M the number of atoms, and 3 the x, y, z coordinates of each atom. This is the order of dimensions required by the neural network, a typical multiPDB has columns in the NxMx3 order.

In [54]:
print(training_set.shape)

torch.Size([1427, 3, 308])


Let's now load the test set in the same way as the training set. This time, we will only retain the coordinates of atoms, normalised and ready to be submitted to the neural network (discarding all other outputs). The test set must contain the same atoms as the training set, in the same order. The two datasets should also be aligned, since *molearn* is not rototranslation invariant.

### 1.3. loading the neural network <a class="anchor" id="ref13"></a>

We can now load the parameters of a trained neural network saved in the following file (variable `networkfile`):

In [55]:
networkfile = f'../run5_alignToOneHelix_foldingnet_checkpoint/checkpoint_epoch43_loss-2.9861797346195704.ckpt'
#network_file = sorted(glob("run1*ProteinH*/checkpoint_epoch83_loss-3.5729515586100833.ckpt"))[0]

Note that the parameters passed to the `AutoEncoder` costructor need to be the same as those used to build the trained neural network.

In [56]:
checkpoint = torch.load(networkfile, map_location=device)

network = AutoEncoder(**checkpoint['network_kwargs'])
network.load_state_dict(checkpoint['model_state_dict'])

network.eval()

AutoEncoder(
  (encoder): Encoder(
    (conv1): Conv1d(12, 64, kernel_size=(1,), stride=(1,))
    (conv2): Conv1d(64, 64, kernel_size=(1,), stride=(1,))
    (conv3): Conv1d(64, 64, kernel_size=(1,), stride=(1,))
    (bn1): BatchNorm1d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    (bn2): BatchNorm1d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    (bn3): BatchNorm1d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    (graph_layer1): GraphLayer(
      (conv): Conv1d(64, 128, kernel_size=(1,), stride=(1,))
      (bn): BatchNorm1d(128, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    )
    (graph_layer2): GraphLayer(
      (conv): Conv1d(128, 1024, kernel_size=(1,), stride=(1,))
      (bn): BatchNorm1d(1024, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    )
    (conv4): Conv1d(1024, 512, kernel_size=(1,), stride=(1,))
    (bn4): BatchNorm1d(512, eps=1e-05, momentum=0.1, affine=True, 

In [57]:
print(next(network.parameters()))

Parameter containing:
tensor([[[ 6.4648e-02],
         [ 5.4243e-02],
         [ 9.1463e-02],
         [-3.4275e-01],
         [-1.0581e-01],
         [ 7.9911e-02],
         [-1.7642e-01],
         [ 7.6580e-02],
         [-2.6070e-01],
         [ 7.9543e-02],
         [-1.9733e-01],
         [-8.9967e-03]],

        [[ 3.1346e-02],
         [-3.0513e-01],
         [-8.2111e-02],
         [ 5.8054e-02],
         [-1.8839e-01],
         [-1.0114e-01],
         [ 3.2722e-01],
         [-9.3934e-02],
         [ 2.6197e-01],
         [ 3.7107e-01],
         [ 2.1740e-01],
         [-1.7816e-01]],

        [[ 1.9213e-02],
         [-7.2258e-02],
         [ 1.6166e-01],
         [ 1.1768e-01],
         [ 1.8172e-01],
         [-3.1172e-01],
         [-1.7130e-01],
         [ 2.7032e-01],
         [-1.9390e-01],
         [ 2.0701e-01],
         [ 2.3107e-01],
         [-8.4117e-02]],

        [[-1.5691e-01],
         [-2.0309e-01],
         [-1.1937e-01],
         [-1.5848e-02],
         [ 2

## 2. Projection into latent space and back <a class="anchor" id="ref2"></a>

Let's start by projecting the whole training set into the latent space. Due to memory constraints we often can't simply encode or decode the entire dataset in one go like:
```
with torch.no_grad():
    z = network.encode(training_set.float())
```
We will need to do this in batches instead.

In [58]:
BATCH_SIZE = 8

def batched_encode(dataset):
    # Preallocate space for the results to go
    z = torch.empty(dataset.shape[0], 2, 1, dtype=dataset.dtype, device = dataset.device)
    with torch.no_grad():
        for i in tqdm(range(0, z.shape[0], BATCH_SIZE)):
            z[i:i+BATCH_SIZE] = network.encode(dataset[i:i+BATCH_SIZE].float())
    return z

def batched_decode(latent_vector, n_atoms):
    decoded = torch.empty(latent_vector.shape[0], 3, n_atoms, dtype=latent_vector.dtype, device = latent_vector.device)
    with torch.no_grad():
        for i in tqdm(range(0, decoded.shape[0], BATCH_SIZE)):
            decoded[i:i+BATCH_SIZE] = network.decode(latent_vector[i:i+BATCH_SIZE].float())[:,:,:n_atoms]
    return decoded

`z` is a (Nx2x1) `Tensor` object, featuring the projection in the latent space of each of the N examples in the training set. If this notebook is running in a computer with a GPU, it will be stored in its memory. To get the data so we can plot it, we should move it back to the CPU, and remove one dimension.

`z` can be decoded back into structures that, hopefully, will closely resemble the training set. Note that we will have to clip the output to the size of dataset's degrees of freedom (an extra padding is present). As for the encoding part, while in principle it is possible to decode all the encoded training set in one shot as follows

```
with torch.no_grad():  
    decoded_training = network.decode(z)[:, :, :training_set.shape[2]]
```
it is often impossible to do so owing to memory constraints. Let's decode our dateset in batches!

`decoded_training` is a now `Tensor` object stored in the GPU with the same dimensionality as the input `training_set`, and features normalised atomic coordinates. While it can already be directly compared with `training_set`, to obtain an actual protein structure we can observe, we should reorder the columns, move the data onto the CPU and "un-normalise" them.

Ok, now let's repeat encoding and decoding with the test set!

## 3. dataset analysis <a class="anchor" id="ref3"></a>

### 3.1. RMSD (or MSE) of input vs autoencoded <a class="anchor" id="ref31"></a>

A way to evaluate the performance of the network, is to compare protein conformations before they are submitted to the neural network, and after they get encoded and decoded. Note that reporting such results for the training set only is poor practice, an independent test set should be submitted to evaluate the ability of the network to generalize beyond the examples provided for training. Let's calculate the MSE of both training and test sets!

In [59]:
import csv
def get_error(network, dataset, meanval, stdval, align=False, mol=""):
    '''
    Calculate the reconstruction error of a dataset encoded and decoded by a trained neural network
    '''

    #z = network.encode(dataset.float())
    z = batched_encode(dataset.float())
    #decoded = network.decode(z)[:,:,:dataset.shape[2]]
    decoded = batched_decode(z, dataset.shape[2])
    err = []
    for i in tqdm(range(dataset.shape[0])):

        crd_ref = dataset[i].permute(1,0).unsqueeze(0).data.cpu().numpy()*stdval + meanval
        crd_mdl = decoded[i].permute(1,0).unsqueeze(0).data.cpu().numpy()[:, :dataset.shape[2]]*stdval + meanval #clip the padding of models  
        if align: # use Molecule Biobox class to calculate RMSD
            mol.coordinates = deepcopy(crd_ref)
            mol.set_current(0)
            mol.add_xyz(crd_mdl[0])
            rmsd = mol.rmsd(0, 1)
        else:
            rmsd = np.sqrt(np.sum((crd_ref.flatten()-crd_mdl.flatten())**2)/crd_mdl.shape[1]) # Cartesian L2 norm

        err.append(rmsd)

    return np.array(err)
    
rmsd_training = get_error(network, training_set, meanval, stdval)
csv_file_path = 'DecodedRMSDOneHelixRun5.csv'

# Save the list/array to a CSV file
with open(csv_file_path, 'w', newline='') as csv_file:
    csv_writer = csv.writer(csv_file)
    csv_writer.writerows(zip(rmsd_training))

#rmsd_test = get_error(network, test_set, meanval, stdval)

100%|████████████████████████████████| 1427/1427 [00:00<00:00, 36190.59it/s]


Time to produce two nice violin plots, reporting on the error of training and test set. Typically the latter will be slightly higher than the former, though ideally this difference should be as small as possible, indicating that the neural network can generalize well to structures it has never seen.

### 3.2. DOPE score of input vs autoencoded <a class="anchor" id="ref32"></a>

The DOPE score is a heuristic function used to estimate the energy of a protein conformation. It is used by software like Modeller to define whether a protein model is accurate. Here, we start by defining a function calculating the DOPE score of a PDB file.

In [60]:
def dope_score(fname):
    env = Environ()
    env.libs.topology.read(file='$(LIB)/top_heav.lib')
    env.libs.parameters.read(file='$(LIB)/par.lib')
    mdl = complete_pdb(env, fname)
    atmsel = Selection(mdl.chains[0])
    score = atmsel.assess_dope()
    return score

A positive value for a DOPE score indicates that the distriution of atoms is not what one should expect from a correct protein conformation (i.e. the protein structure is bad). However, a negative DOPE score does not immediately tell us how good the structure is. To tell whether the models generated by the neural network are good, we will compare their DOPE score with the DOPE score of the input dataset, that we can assume being good. We now calculate the DOPE score of the training and test sets.

In [61]:
def get_dope(network, dataset, meanval, stdval, mol):
    
    # set residues names with protonated histidines back to generic HIS name (needed by DOPE score function)
    testH = mol.data["resname"].values
    testH[testH == "HIE"] = "HIS"
    testH[testH == "HID"] = "HIS"
    mol.data["resname"] = testH

    #z = network.encode(dataset.float())
    z = batched_encode(dataset.float())
    #decoded = network.decode(z)[:,:,:dataset.shape[2]]
    decoded = batched_decode(z, dataset.shape[2])
    
    dope_dataset = []
    dope_decoded = []
    for i in tqdm(range(dataset.shape[0])):

        # calculate DOPE score of input dataset
        crd_ref = dataset[i].permute(1,0).unsqueeze(0).data.cpu().numpy()*stdval + meanval
        mol.coordinates = deepcopy(crd_ref)
        mol.write_pdb("tmp.pdb")
        s = dope_score("tmp.pdb")
        dope_dataset.append(s)

        # calculate DOPE score of decoded counterpart
        crd_mdl = decoded[i].permute(1,0).unsqueeze(0).data.cpu().numpy()[:, :dataset.shape[2]]*stdval + meanval  
        mol.coordinates = deepcopy(crd_mdl)
        mol.write_pdb("tmp.pdb")
        s = dope_score("tmp.pdb")
        dope_decoded.append(s)
    
    return dope_dataset, dope_decoded
 
dope_training, dope_training_decoded = get_dope(network, training_set, meanval, stdval, mol)
csv_file_path = 'DecodedDOPEOneHelixRun5.csv'

# Save the list/array to a CSV file
with open(csv_file_path, 'w', newline='') as csv_file:
    csv_writer = csv.writer(csv_file)
    csv_writer.writerows(zip(dope_training_decoded))
#dope_test, dope_test_decoded = get_dope(network, test_set, meanval, stdval, mol)

  0%|                                      | 1/1427 [00:00<07:45,  3.06it/s]

read_to_681_> topology.submodel read from topology file:        3
read_pd_459W> Residue type  ACE not recognized. 'AutoModel' model building
              will treat this residue as a rigid body.
              To use real parameters, add the residue type to ${LIB}/restyp.lib,
              its topology to ${LIB}/top_*.lib, and suitable forcefield
              parameters to ${LIB}/par.lib.
rdpdb___459W> Residue type  NME not recognized. 'AutoModel' model building
              will treat this residue as a rigid body.
              To use real parameters, add the residue type to ${LIB}/restyp.lib,
              its topology to ${LIB}/top_*.lib, and suitable forcefield
              parameters to ${LIB}/par.lib.
>> Model assessment by DOPE potential
iatmcls_286W> MODEL atom not classified:  ACE:C  ACE
iatmcls_286W> MODEL atom not classified:  ACE:O  ACE
iatmcls_286W> MODEL atom not classified:  NME:N  NME
preppdf_453W> No fixed restraints selected; there may be some dynamic ones.
preppdf

  0%|                                      | 2/1427 [00:00<07:00,  3.39it/s]

read_to_681_> topology.submodel read from topology file:        3
read_pd_459W> Residue type  ACE not recognized. 'AutoModel' model building
              will treat this residue as a rigid body.
              To use real parameters, add the residue type to ${LIB}/restyp.lib,
              its topology to ${LIB}/top_*.lib, and suitable forcefield
              parameters to ${LIB}/par.lib.
rdpdb___459W> Residue type  NME not recognized. 'AutoModel' model building
              will treat this residue as a rigid body.
              To use real parameters, add the residue type to ${LIB}/restyp.lib,
              its topology to ${LIB}/top_*.lib, and suitable forcefield
              parameters to ${LIB}/par.lib.
>> Model assessment by DOPE potential
iatmcls_286W> MODEL atom not classified:  ACE:C  ACE
iatmcls_286W> MODEL atom not classified:  ACE:O  ACE
iatmcls_286W> MODEL atom not classified:  NME:N  NME
preppdf_453W> No fixed restraints selected; there may be some dynamic ones.
preppdf

  0%|                                      | 3/1427 [00:00<06:45,  3.51it/s]

...

read_to_681_> topology.submodel read from topology file:        3
read_pd_459W> Residue type  ACE not recognized. 'AutoModel' model building
              will treat this residue as a rigid body.
              To use real parameters, add the residue type to ${LIB}/restyp.lib,
              its topology to ${LIB}/top_*.lib, and suitable forcefield
              parameters to ${LIB}/par.lib.
rdpdb___459W> Residue type  NME not recognized. 'AutoModel' model building
              will treat this residue as a rigid body.
              To use real parameters, add the residue type to ${LIB}/restyp.lib,
              its topology to ${LIB}/top_*.lib, and suitable forcefield
              parameters to ${LIB}/par.lib.
>> Model assessment by DOPE potential
iatmcls_286W> MODEL atom not classified:  ACE:C  ACE
iatmcls_286W> MODEL atom not classified:  ACE:O  ACE
iatmcls_286W> MODEL atom not classified:  NME:N  NME
preppdf_453W> No fixed restraints selected; there may be some dynamic ones.
preppdf

100%|██████████████████████████████████▉| 1426/1427 [06:31<00:00,  3.66it/s]

read_to_681_> topology.submodel read from topology file:        3
read_pd_459W> Residue type  ACE not recognized. 'AutoModel' model building
              will treat this residue as a rigid body.
              To use real parameters, add the residue type to ${LIB}/restyp.lib,
              its topology to ${LIB}/top_*.lib, and suitable forcefield
              parameters to ${LIB}/par.lib.
rdpdb___459W> Residue type  NME not recognized. 'AutoModel' model building
              will treat this residue as a rigid body.
              To use real parameters, add the residue type to ${LIB}/restyp.lib,
              its topology to ${LIB}/top_*.lib, and suitable forcefield
              parameters to ${LIB}/par.lib.
>> Model assessment by DOPE potential
iatmcls_286W> MODEL atom not classified:  ACE:C  ACE
iatmcls_286W> MODEL atom not classified:  ACE:O  ACE
iatmcls_286W> MODEL atom not classified:  NME:N  NME
preppdf_453W> No fixed restraints selected; there may be some dynamic ones.
preppdf

100%|███████████████████████████████████| 1427/1427 [06:32<00:00,  3.64it/s]

read_to_681_> topology.submodel read from topology file:        3
read_pd_459W> Residue type  ACE not recognized. 'AutoModel' model building
              will treat this residue as a rigid body.
              To use real parameters, add the residue type to ${LIB}/restyp.lib,
              its topology to ${LIB}/top_*.lib, and suitable forcefield
              parameters to ${LIB}/par.lib.
rdpdb___459W> Residue type  NME not recognized. 'AutoModel' model building
              will treat this residue as a rigid body.
              To use real parameters, add the residue type to ${LIB}/restyp.lib,
              its topology to ${LIB}/top_*.lib, and suitable forcefield
              parameters to ${LIB}/par.lib.
>> Model assessment by DOPE potential
iatmcls_286W> MODEL atom not classified:  ACE:C  ACE
iatmcls_286W> MODEL atom not classified:  ACE:O  ACE
iatmcls_286W> MODEL atom not classified:  NME:N  NME
preppdf_453W> No fixed restraints selected; there may be some dynamic ones.
preppdf

---